In [1]:
import pandas as pd
import os
import s3fs
import warnings
from datetime import date, timedelta, datetime
import numpy as np

In [2]:
# Import KPI construction functions
#exec(open('0_KPI_functions.py').read())
exec(open('../0_KPI_functions.py').read())


In [3]:
# Create filesystem object
S3_ENDPOINT_URL = "https://" + os.environ["AWS_S3_ENDPOINT"]
fs = s3fs.S3FileSystem(client_kwargs={'endpoint_url': S3_ENDPOINT_URL})

BUCKET = "projet-bdc2324-team1/0_Input/Company_10"
fs.ls(BUCKET)

['projet-bdc2324-team1/0_Input/Company_10/campaigns_information.csv',
 'projet-bdc2324-team1/0_Input/Company_10/customerplus_cleaned.csv',
 'projet-bdc2324-team1/0_Input/Company_10/products_purchased_reduced.csv',
 'projet-bdc2324-team1/0_Input/Company_10/target_information.csv']

In [4]:
dic_base=['campaigns_information','customerplus_cleaned','products_purchased_reduced','target_information']
for nom_base in dic_base:
    FILE_PATH_S3_fanta = 'projet-bdc2324-team1/0_Input/Company_10/' + nom_base + '.csv'
    with fs.open(FILE_PATH_S3_fanta, mode="rb") as file_in:
        globals()[nom_base] = pd.read_csv(file_in, sep=",")

In [5]:

def display_databases(directory_path, file_name, datetime_col = None):
    """
    This function returns the file from s3 storage 
    """
    file_path = "projet-bdc2324-team1" + "/0_Input/Company_" + directory_path + "/" + file_name + ".csv"
    print("File path : ", file_path)
    with fs.open(file_path, mode="rb") as file_in:
        df = pd.read_csv(file_in, sep=",", parse_dates = datetime_col, date_parser=custom_date_parser)        
    return df 


nb_compagnie=['10','11','12','13','14']
for directory_path in nb_compagnie:
    df_customerplus_clean = display_databases(directory_path, file_name = "customerplus_cleaned")
    df_campaigns_information = display_databases(directory_path, file_name = "campaigns_information", datetime_col = ['opened_at', 'sent_at', 'campaign_sent_at'])
    df_products_purchased_reduced = display_databases(directory_path, file_name = "products_purchased_reduced", datetime_col = ['purchase_date'])
    df_customerplus_clean["Number_compagnie"]=int(directory_path)
    df_campaigns_information["Number_compagnie"]=int(directory_path)
    df_products_purchased_reduced["Number_compagnie"]=int(directory_path)

    if nb_compagnie.index(directory_path)>=1:
        customerplus_clean_spectacle=pd.concat([customerplus_clean_spectacle,df_customerplus_clean],axis=0)
        campaigns_information_spectacle=pd.concat([campaigns_information_spectacle,df_campaigns_information],axis=0)
        products_purchased_reduced_spectacle=pd.concat([products_purchased_reduced_spectacle,df_products_purchased_reduced],axis=0)
    else:
        customerplus_clean_spectacle=df_customerplus_clean
        campaigns_information_spectacle=df_campaigns_information
        products_purchased_reduced_spectacle=df_products_purchased_reduced
        

In [6]:
#creation de KPI aggreger par thématique

nb_compagnie=['10','11','12','13','14']
for directory_path in nb_compagnie:
    df_customerplus_clean_0 = display_databases(directory_path, file_name = "customerplus_cleaned")
    df_campaigns_information = display_databases(directory_path, file_name = "campaigns_information", datetime_col = ['opened_at', 'sent_at', 'campaign_sent_at'])
    df_products_purchased_reduced = display_databases(directory_path, file_name = "products_purchased_reduced", datetime_col = ['purchase_date'])
    df_campaigns_kpi = campaigns_kpi_function(campaigns_information = df_campaigns_information) 
    df_tickets_kpi = tickets_kpi_function(tickets_information = df_products_purchased_reduced)
    df_customerplus_clean = customerplus_kpi_function(customerplus_clean = df_customerplus_clean_0)
    
#creation de la colonne Number compagnie
    df_tickets_kpi["Number_compagnie"]=int(directory_path)
    df_campaigns_kpi["Number_compagnie"]=int(directory_path)
    df_customerplus_clean["Number_compagnie"]=int(directory_path)

    if nb_compagnie.index(directory_path)>=1:
        customerplus_clean_spectacle=pd.concat([customerplus_clean_spectacle,df_customerplus_clean],axis=0)
        campaigns_information_spectacle=pd.concat([campaigns_information_spectacle,df_campaigns_kpi],axis=0)
        products_purchased_reduced_spectacle=pd.concat([products_purchased_reduced_spectacle,df_tickets_kpi],axis=0)
    else:
        customerplus_clean_spectacle=df_customerplus_clean
        campaigns_information_spectacle=df_campaigns_kpi
        products_purchased_reduced_spectacle=df_tickets_kpi

File path :  projet-bdc2324-team1/0_Input/Company_10/customerplus_cleaned.csv


/tmp/ipykernel_8330/2987234667.py:8: FutureWarning: The argument 'date_parser' is deprecated and will be removed in a future version. Please use 'date_format' instead, or read your data in as 'object' dtype and then call 'to_datetime'.
  df = pd.read_csv(file_in, sep=",", parse_dates = datetime_col, date_parser=custom_date_parser)


File path :  projet-bdc2324-team1/0_Input/Company_10/campaigns_information.csv


/tmp/ipykernel_8330/2987234667.py:8: FutureWarning: The argument 'date_parser' is deprecated and will be removed in a future version. Please use 'date_format' instead, or read your data in as 'object' dtype and then call 'to_datetime'.
  df = pd.read_csv(file_in, sep=",", parse_dates = datetime_col, date_parser=custom_date_parser)


File path :  projet-bdc2324-team1/0_Input/Company_10/products_purchased_reduced.csv


...

/tmp/ipykernel_8330/2987234667.py:8: FutureWarning: The argument 'date_parser' is deprecated and will be removed in a future version. Please use 'date_format' instead, or read your data in as 'object' dtype and then call 'to_datetime'.
  df = pd.read_csv(file_in, sep=",", parse_dates = datetime_col, date_parser=custom_date_parser)


File path :  projet-bdc2324-team1/0_Input/Company_14/campaigns_information.csv


/tmp/ipykernel_8330/2987234667.py:8: FutureWarning: The argument 'date_parser' is deprecated and will be removed in a future version. Please use 'date_format' instead, or read your data in as 'object' dtype and then call 'to_datetime'.
  df = pd.read_csv(file_in, sep=",", parse_dates = datetime_col, date_parser=custom_date_parser)


File path :  projet-bdc2324-team1/0_Input/Company_14/products_purchased_reduced.csv


/tmp/ipykernel_8330/2987234667.py:8: FutureWarning: The argument 'date_parser' is deprecated and will be removed in a future version. Please use 'date_format' instead, or read your data in as 'object' dtype and then call 'to_datetime'.
  df = pd.read_csv(file_in, sep=",", parse_dates = datetime_col, date_parser=custom_date_parser)
/tmp/ipykernel_8330/2987234667.py:8: DtypeWarning: Columns (8,9) have mixed types. Specify dtype option on import or set low_memory=False.
  df = pd.read_csv(file_in, sep=",", parse_dates = datetime_col, date_parser=custom_date_parser)
<string>:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy


In [7]:
customerplus_clean_spectacle

customer_id  street_id  structure_id  mcp_contact_id  fidelity  \
0            821538        139           NaN             NaN         0   
1            809126       1063           NaN             NaN         0   
2             11005       1063           NaN             NaN         0   
3             17663      12731           NaN             NaN         0   
4             38100      12395           NaN             NaN         0   
...             ...        ...           ...             ...       ...   
343121      4667645        122           NaN       1534181.0         0   
343122      4667649        122           NaN       1534177.0         0   
343123      4667660        122           NaN       1534165.0         0   
343124      4667679        122           NaN       1534132.0         0   
343125      4667686        122           NaN       1567949.0         0   

        tenant_id  is_partner  deleted_at  gender  is_email_true  ...  \
0             875       False         NaN       2           True  ...   
1             875       False         NaN       2           True  ...   
2             875       False         NaN       2          False  ...   
3             875       False         NaN       0          False  ...   
4             875       False         NaN       0           True  ...   
...           ...         ...         ...     ...            ...  ...   
343121        862       False         NaN       2           True  ...   
343122        862       False         NaN       2           True  ...   
343123        862       False         NaN       0           True  ...   
343124        862       False         NaN       2           True  ...   
343125        862       False         NaN       0           True  ...   

        purchase_count first_buying_date  country  gender_label  \
0                    0               NaN      NaN         other   
1                    0               NaN       fr         other   
2                   14               NaN       fr         other   
3                    1               NaN       fr        female   
4                    1               NaN       fr        female   
...                ...               ...      ...           ...   
343121               0               NaN      NaN         other   
343122               0               NaN      NaN         other   
343123               0               NaN      NaN        female   
343124               0               NaN      NaN         other   
343125               0               NaN      NaN        female   

        gender_female  gender_male  gender_other  country_fr  has_tags  \
0                   0            0             1         NaN         0   
1                   0            0             1         1.0         0   
2                   0            0             1         1.0         0   
3                   1            0             0         1.0         0   
4                   1            0             0         1.0         0   
...               ...          ...           ...         ...       ...   
343121              0            0             1         NaN         0   
343122              0            0             1         NaN         0   
343123              1            0             0         NaN         0   
343124              0            0             1         NaN         0   
343125              1            0             0         NaN         0   

        Number_compagnie  
0                     10  
1                     10  
2                     10  
3                     10  
4                     10  
...                  ...  
343121                14  
343122                14  
343123                14  
343124                14  
343125                14  

[1523688 rows x 29 columns]

In [8]:
campaigns_information_spectacle

customer_id  nb_campaigns  nb_campaigns_opened    time_to_open  \
0                29             4                  0.0             NaT   
1                37             3                  0.0             NaT   
2                39             4                  1.0 0 days 05:16:38   
3                41             4                  1.0 0 days 01:12:29   
4                44             4                  0.0             NaT   
...             ...           ...                  ...             ...   
254699      6837769             1                  1.0 0 days 23:42:15   
254700      6875038             1                  0.0             NaT   
254701      6875066             1                  0.0             NaT   
254702      6875099             1                  0.0             NaT   
254703      6875143             1                  1.0 0 days 01:17:01   

        Number_compagnie  
0                     10  
1                     10  
2                     10  
3                     10  
4                     10  
...                  ...  
254699                14  
254700                14  
254701                14  
254702                14  
254703                14  

[688953 rows x 5 columns]

In [9]:
products_purchased_reduced_spectacle

customer_id  nb_tickets  nb_purchases  total_amount  nb_suppliers  \
0            19482          88            29         872.0             2   
1            19484           3             2          62.0             1   
2            19485         131            21        1878.0             2   
3            19486          10             4          96.0             1   
4            19487           2             1          33.0             1   
...            ...         ...           ...           ...           ...   
99580      6884747           2             1          40.0             1   
99581      6884748           2             1          40.0             1   
99582      6884750           4             1          80.0             1   
99583      6884751           2             1          40.0             1   
99584      6884753           2             1          40.0             1   

       vente_internet_max  purchase_date_min  purchase_date_max  \
0                       1        2643.092500         718.149398   
1                       0        1745.021736        1743.045035   
2                       1        2649.044745          85.240845   
3                       0        1944.077604        1742.794225   
4                       0        1742.877766        1742.877766   
...                   ...                ...                ...   
99580                   0           0.193750           0.193750   
99581                   0           0.186806           0.186806   
99582                   0           0.136111           0.136111   
99583                   0           0.122917           0.122917   
99584                   0           0.047222           0.047222   

       time_between_purchase  nb_tickets_internet  Number_compagnie  
0                1924.943102                  8.0                10  
1                   1.976701                  0.0                10  
2                2563.803900                 84.0                10  
3                 201.283380                  0.0                10  
4                   0.000000                  0.0                10  
...                      ...                  ...               ...  
99580               0.000000                  0.0                14  
99581               0.000000                  0.0                14  
99582               0.000000                  0.0                14  
99583               0.000000                  0.0                14  
99584               0.000000                  0.0                14  

[764880 rows x 11 columns]